In [1]:
pip install flask numpy pandas yfinance scikit-learn alpaca-trade-api


Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install flask numpy pandas yfinance scikit-learn

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install ipywidgets yfinance pandas numpy scikit-learn alpaca-trade-api

Note: you may need to restart the kernel to use updated packages.


In [4]:
# Import necessary libraries
from flask import Flask, render_template_string, request, jsonify
import os
import time
import numpy as np
import pandas as pd
import yfinance as yf
from sklearn.linear_model import LinearRegression
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import LimitOrderRequest
from alpaca.trading.enums import OrderSide, TimeInForce
import threading
import logging
import socket
from datetime import datetime

# Configure logging for debugging
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Initialize Flask app
app = Flask(__name__)
app.secret_key = 'your_secure_secret_key_here'  # Use a secure, random key in production

# Global variables to store API keys, trading client, and trader instance
ALPACA_API_KEY = None
ALPACA_SECRET_KEY = None
trading_client = None
trader = None
thread = None

# MLTrader class
class MLTrader:
    def __init__(self, api_key, secret_key, symbol=None):
        if not symbol or not isinstance(symbol, str) or symbol.strip() == "":
            raise ValueError("Stock symbol must be provided and cannot be empty")
        self.api_key = api_key.strip()  # Strip whitespace
        self.secret_key = secret_key.strip()  # Strip whitespace
        self.symbol = symbol.upper()
        self.running = False
        self.profit_history = []  # Store profits/losses
        self.trade_history = []  # Store buy/sell actions for visualization
        self.inventory = []  # Holds buy prices
        try:
            self.trading_client = TradingClient(self.api_key, self.secret_key, paper=True)
            self.trading_client.get_account()  # Test connection immediately
            logger.info(f"Successfully initialized TradingClient for {self.symbol}")
        except Exception as e:
            logger.error(f"Failed to initialize TradingClient for {self.symbol}: {str(e)}")
            raise ValueError(f"Invalid API keys or connection failed: {str(e)}")
        self.window_size = 10
        self.model = LinearRegression()
        self.data = self.load_data()
        self.last_trade_time = None

    def load_data(self):
        try:
            end_date = datetime.now().strftime('%Y-%m-%d')
            dataset = yf.download(self.symbol, start="2024-01-01", end=end_date, progress=False)
            if dataset.empty:
                logger.warning(f"No data available for {self.symbol} from yfinance, using mock data")
                dates = pd.date_range('2025-02-10', '2025-02-24', freq='D')
                prices = [129.50, 130.00, 131.50, 132.00, 133.10, 134.00, 133.80, 132.90, 133.50, 132.00, 134.50, 134.43, 135.00, 134.20, 135.30]
                return pd.Series(prices, index=dates)
            return dataset['Close']
        except Exception as e:
            logger.error(f"❌ Failed to load data for {self.symbol}: {e}")
            raise ValueError(f"Failed to load data for {self.symbol}: {str(e)}")

    def train(self):
        if len(self.data) < self.window_size + 1:
            raise ValueError(f"Data length ({len(self.data)}) is insufficient for window size {self.window_size}")
        X, y = [], []
        for i in range(len(self.data) - self.window_size):
            X.append(self.data.iloc[i:i + self.window_size].values)
            y.append(self.data.iloc[i + self.window_size])
        X = np.array(X).reshape(len(X), -1)
        y = np.array(y)
        try:
            self.model.fit(X, y)
            return f"Model R² Score: {self.model.score(X, y):.4f}"
        except Exception as e:
            logger.error(f"Failed to train model for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to train model: {str(e)}")

    def predict(self, recent_data):
        if len(recent_data) < self.window_size:
            logger.warning(f"Insufficient data for prediction for {self.symbol}")
            return None
        try:
            return self.model.predict(np.array(recent_data).reshape(1, -1))[0]
        except Exception as e:
            logger.error(f"Prediction error for {self.symbol}: {str(e)}")
            return None

    def get_realtime_price(self):
        try:
            quote = self.trading_client.get_latest_quote(self.symbol)
            if quote and quote.ask_price:
                return quote.ask_price
            logger.warning(f"No ask price from Alpaca for {self.symbol}, trying yfinance")
            latest_data = yf.download(self.symbol, period="1d", interval="1m", progress=False)["Close"]
            if not latest_data.empty:
                return latest_data.iloc[-1]
            raise ValueError(f"No price data available for {self.symbol}")
        except Exception as e:
            logger.error(f"Error fetching real-time price for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to fetch price for {self.symbol}: {str(e)}")

    def place_order(self, qty, side, limit_price):
        try:
            rounded_price = round(limit_price, 2)
            order = LimitOrderRequest(
                symbol=self.symbol,
                qty=qty,
                side=side,
                time_in_force=TimeInForce.DAY,
                limit_price=rounded_price
            )
            order_result = self.trading_client.submit_order(order)
            action = f"{side.name} {qty} shares of {self.symbol} at ${rounded_price}"
            self.trade_history.append({
                "time": pd.Timestamp.now().strftime("%Y-%m-%d %H:%M:%S"),
                "action": action,
                "price": rounded_price
            })
            self.last_trade_time = pd.Timestamp.now()
            logger.info(f"✅ Order placed: {action}")
            return f"Placed {side.name} order for {qty} shares at ${rounded_price}"
        except Exception as e:
            logger.error(f"❌ Error placing {side.name} order for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to place {side.name} order: {str(e)}")

    def run(self):
        self.running = True
        try:
            self.data = self.load_data()
            self.train()
            recent_data = self.data.values[-self.window_size:]
            
            while self.running:
                try:
                    current_price = self.get_realtime_price()
                    if current_price is None:
                        logger.warning(f"No real-time price for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    predicted_price = self.predict(recent_data)
                    if predicted_price is None:
                        logger.warning(f"Prediction failed for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    if self.last_trade_time:
                        time_since_last_trade = (pd.Timestamp.now() - self.last_trade_time).total_seconds()
                        if time_since_last_trade < 60:
                            time.sleep(60 - time_since_last_trade)

                    logger.debug(f"{self.symbol} - Current Price: ${current_price:.2f}, Predicted Price: ${predicted_price:.2f}")
                    
                    if predicted_price > current_price * 1.001 and not self.inventory:  # Buy if 0.1% above
                        self.inventory.append(current_price)
                        self.place_order(10, OrderSide.BUY, current_price)
                    elif predicted_price < current_price * 0.999 and self.inventory:  # Sell if 0.1% below
                        buy_price = self.inventory.pop(0)
                        profit = round(current_price - buy_price, 2)
                        self.profit_history.append(profit)
                        self.place_order(10, OrderSide.SELL, current_price)

                    new_data = yf.download(self.symbol, start=pd.Timestamp.now() - pd.Timedelta(days=1), end=pd.Timestamp.now(), progress=False)["Close"]
                    if not new_data.empty:
                        self.data = pd.concat([self.data, new_data]).drop_duplicates()
                        recent_data = self.data.values[-self.window_size:]
                    time.sleep(60)  # Wait 60 seconds between checks
                except Exception as e:
                    logger.error(f"Error in trading loop for {self.symbol}: {str(e)}")
                    time.sleep(60)
                    continue
        except Exception as e:
            logger.error(f"Failed to start trading loop for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to start trading: {str(e)}")

    def stop(self):
        self.running = False
        logger.info(f"Stopped trading for {self.symbol}")

    def get_stats(self):
        accuracy = 0.0  # Placeholder, to be calculated based on trade history
        total_trades = len(self.trade_history)
        total_profit_loss = sum(self.profit_history) if self.profit_history else 0.0
        latest_trade = self.trade_history[-1] if self.trade_history else None
        last_trade_time = (pd.Timestamp.now() - pd.Timestamp(self.last_trade_time)).total_seconds() / 60 if self.last_trade_time else 0
        return {
            "latest_action": latest_trade["action"] if latest_trade else "None",
            "latest_price": f"${latest_trade['price']:.2f}" if latest_trade else "$0.00",
            "last_trade_time": f"{last_trade_time:.1f}" if last_trade_time > 0 else "0",
            "model_accuracy": f"{accuracy:.1f}%",
            "precision": "0.0%",  # Placeholder
            "recall": "0.0%",     # Placeholder
            "prediction_confidence": "0.0%",  # Placeholder
            "mse": "0.000000",    # Placeholder
            "win_rate": "0.0%"     # Placeholder
        }

# Flask routes
@app.route('/')
def home():
    return render_template_string(dashboard_html)

@app.route('/set_api_keys', methods=['POST'])
def set_api_keys():
    global ALPACA_API_KEY, ALPACA_SECRET_KEY, trading_client
    data = request.get_json()
    if not data:
        return jsonify({'status': 'error', 'message': 'No data provided'}), 400

    ALPACA_API_KEY = data.get('api_key', '').strip()
    ALPACA_SECRET_KEY = data.get('secret_key', '').strip()

    if not ALPACA_API_KEY or not ALPACA_SECRET_KEY:
        return jsonify({'status': 'error', 'message': 'API key and secret key are required'}), 400

    try:
        trading_client = TradingClient(ALPACA_API_KEY, ALPACA_SECRET_KEY, paper=True)
        account = trading_client.get_account()  # Test connection
        logger.info(f"API keys set successfully. Account status: {account.status}")
        return jsonify({'status': 'success', 'message': 'API keys set successfully'})
    except Exception as e:
        logger.error(f"Invalid API keys: {str(e)}")
        return jsonify({'status': 'error', 'message': f'Invalid API keys: {str(e)}'}), 400

@app.route('/start_trading', methods=['POST'])
def start_trading():
    global trader, thread
    data = request.get_json()
    if not data:
        return jsonify({'status': 'error', 'message': 'No data provided'}), 400

    stock_symbol = data.get('stock_symbol', '').strip()
    if not stock_symbol:
        return jsonify({'status': 'error', 'message': 'Stock symbol is required'}), 400

    if not ALPACA_API_KEY or not ALPACA_SECRET_KEY:
        return jsonify({'status': 'error', 'message': 'API keys must be set before trading'}), 400

    if trader and trader.running:
        return jsonify({'status': 'warning', 'message': f'Bot already running for {trader.symbol}'})

    try:
        trader = MLTrader(ALPACA_API_KEY, ALPACA_SECRET_KEY, stock_symbol)
        logger.info(f"Starting bot for symbol: {stock_symbol}")
        thread = threading.Thread(target=trader.run, daemon=True)
        thread.start()
        return jsonify({'status': 'success', 'message': f'Trading started for {stock_symbol}'})
    except ValueError as e:
        logger.error(f"Error initializing trader for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 400
    except Exception as e:
        logger.error(f"Unexpected error starting trading for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 500

@app.route('/stop_trading', methods=['POST'])
def stop_trading():
    global trader, thread
    if trader and trader.running:
        trader.stop()
        if thread:
            thread.join(timeout=5)
        stats = trader.get_stats()
        trader = None
        thread = None
        logger.info("Bot stopped")
        return jsonify({'status': 'success', 'stats': stats})
    return jsonify({'status': 'warning', 'message': 'Bot is not running'})

@app.route('/status')
def status():
    if trader and trader.running:
        stats = trader.get_stats()
        return jsonify({'status': 'running', **stats})
    return jsonify({'status': 'stopped', 'latest_action': 'None', 'latest_price': '$0.00', 'last_trade_time': '0', 'model_accuracy': '0.0%', 'precision': '0.0%', 'recall': '0.0%', 'prediction_confidence': '0.0%', 'mse': '0.000000', 'win_rate': '0.0%'})

# Dashboard HTML template as a string
dashboard_html = '''
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>ML Trading Bot Dashboard</title>
    <link href="https://cdn.jsdelivr.net/npm/tailwindcss@2.2.19/dist/tailwind.min.css" rel="stylesheet">
    <link href="https://fonts.googleapis.com/css2?family=Roboto:wght@400;700&display=swap" rel="stylesheet">
    <script src="https://cdn.plotly.com/plotly-latest.min.js"></script>
</head>
<body class="bg-black text-white">
    <div class="container mx-auto p-6">
        <h1 class="text-3xl font-bold mb-6 text-center">ML Trading Bot Dashboard</h1>
        <div class="controls bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <form id="apiForm" method="POST" class="space-y-4">
                <div>
                    <label class="block text-sm font-medium mb-2">Alpaca API Key</label>
                    <input type="text" name="api_key" id="api_key" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter API Key" required>
                </div>
                <div>
                    <label class="block text-sm font-medium mb-2">Alpaca Secret Key</label>
                    <input type="password" name="secret_key" id="secret_key" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Secret Key" required>
                </div>
                <button type="submit" class="w-full bg-purple-600 hover:bg-purple-700 text-white p-3 rounded font-bold transition-colors">Set API Keys</button>
            </form>
            <form id="tradingForm" method="POST" class="space-y-4 mt-4">
                <div>
                    <label class="block text-sm font-medium mb-2">Stock Symbol</label>
                    <input type="text" name="stock_symbol" id="stock_symbol" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Stock Symbol (e.g., NVDA)" required pattern="[A-Z]{1,5}" title="Enter 1-5 uppercase letters (e.g., NVDA)">
                </div>
                <div class="flex space-x-4">
                    <button type="submit" name="action" value="start" class="w-full bg-green-600 hover:bg-green-700 text-white p-3 rounded font-bold transition-colors">Start Trading</button>
                    <button type="submit" name="action" value="stop" class="w-full bg-red-600 hover:bg-red-700 text-white p-3 rounded font-bold transition-colors">Stop Trading</button>
                </div>
            </form>
            {% with messages = get_flashed_messages(with_categories=true) %}
                {% if messages %}
                    {% for category, message in messages %}
                        <div class="mt-4 text-center {{ 'text-red-500' if category == 'error' else 'text-yellow-500' if category == 'warning' else 'text-green-500' if category == 'success' else 'text-gray-500' }}">
                            {{ message }}
                        </div>
                    {% endfor %}
                {% endif %}
            {% endwith %}
        </div>
        <div class="stats bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <h2 class="text-xl font-semibold mb-4">Latest Trade</h2>
            <p>Action: <span id="latest_action">None</span></p>
            <p>Price: <span id="latest_price">$0.00</span></p>
            <p>Last trade was <span id="last_trade_time">0</span> minutes ago</p>
        </div>
        <div class="performance bg-gray-900 p-6 rounded-lg shadow-lg">
            <h2 class="text-xl font-semibold mb-4">ML Model Performance</h2>
            <p>Model Accuracy: <span id="model_accuracy">0.0%</span></p>
            <p>Precision: <span id="precision">0.0%</span></p>
            <p>Recall: <span id="recall">0.0%</span></p>
            <p>Prediction Confidence: <span id="prediction_confidence">0.0%</span></p>
            <p>Mean Squared Error: <span id="mse">0.000000</span></p>
            <p>Win Rate: <span id="win_rate">0.0%</span></p>
        </div>
    </div>
    <script>
        async function updateStatus() {
            try {
                const response = await fetch('/status', { headers: { 'Accept': 'application/json' } });
                if (!response.ok) {
                    const text = await response.text();
                    throw new Error(`Server error: ${text || 'Failed to fetch status'}`);
                }
                const data = await response.json();
                document.getElementById('latest_action').textContent = data.latest_action;
                document.getElementById('latest_price').textContent = data.latest_price;
                document.getElementById('last_trade_time').textContent = data.last_trade_time;
                document.getElementById('model_accuracy').textContent = data.model_accuracy;
                document.getElementById('precision').textContent = data.precision;
                document.getElementById('recall').textContent = data.recall;
                document.getElementById('prediction_confidence').textContent = data.prediction_confidence;
                document.getElementById('mse').textContent = data.mse;
                document.getElementById('win_rate').textContent = data.win_rate;
            } catch (error) {
                console.error('Error updating status:', error);
                document.getElementById('latest_action').textContent = 'Error';
                document.getElementById('latest_price').textContent = '$0.00';
                document.getElementById('last_trade_time').textContent = '0';
                alert(`Status update failed: ${error.message}`);
            }
        }
        setInterval(updateStatus, 2000); // Update every 2 seconds
        updateStatus();

        document.getElementById('apiForm').addEventListener('submit', async (e) => {
            e.preventDefault();
            const formData = new FormData(e.target);
            const apiKey = formData.get('api_key')?.trim();
            const secretKey = formData.get('secret_key')?.trim();
            if (!apiKey || !secretKey) {
                alert('Please enter both API Key and Secret Key');
                return;
            }
            try {
                const response = await fetch('/set_api_keys', {
                    method: 'POST',
                    headers: { 'Content-Type': 'application/json', 'Accept': 'application/json' },
                    body: JSON.stringify({ api_key: apiKey, secret_key: secretKey })
                });
                const data = await response.json();
                if (!response.ok) {
                    throw new Error(data.message || 'Failed to set API keys');
                }
                alert('API keys set successfully');
            } catch (error) {
                console.error('Error setting API keys:', error);
                alert('Failed to set API keys: ' + error.message);
            }
        });

        document.getElementById('tradingForm').addEventListener('submit', async (e) => {
            e.preventDefault();
            const formData = new FormData(e.target);
            const stockSymbol = formData.get('stock_symbol')?.trim();
            const action = formData.get('action');
            if (!stockSymbol) {
                alert('Please enter a valid stock symbol (1-5 uppercase letters, e.g., NVDA)');
                return;
            }
            try {
                const response = await fetch(`/${action}_trading`, {
                    method: 'POST',
                    headers: { 'Content-Type': 'application/json', 'Accept': 'application/json' },
                    body: JSON.stringify({ stock_symbol: stockSymbol })
                });
                const data = await response.json();
                if (!response.ok) {
                    throw new Error(data.message || 'Server error');
                }
                alert(data.message);
                updateStatus(); // Refresh stats after action
            } catch (error) {
                console.error(`Error ${action} trading:`, error);
                alert(`Failed to ${action} trading: ${error.message}`);
            }
        });
    </script>
</body>
</html>
'''

# Function to run the Flask app in a separate thread
def run_flask():
    app.run(debug=True, use_reloader=False, host='0.0.0.0', port=5000)  # Re-enabled debug for detailed logging

# Display the dashboard in the notebook and start Flask
if __name__ == '__main__':
    try:
        # Start Flask in a separate thread
        flask_thread = threading.Thread(target=run_flask, daemon=True)
        flask_thread.start()
        
        # Get local IP for network access
        local_ip = '127.0.0.1'  # Default to localhost
        try:
            s = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
            s.connect(('8.8.8.8', 80))  # Google DNS
            local_ip = s.getsockname()[0]
            s.close()
            logger.info(f"Local IP detected: {local_ip}")
        except Exception as e:
            logger.error(f"Failed to detect local IP: {e}")

        # Display in Jupyter (optional, for notebook use)
        display(HTML(f"""
            <h2>ML Trading Bot Interface</h2>
            <p>Access the trading bot at <a href="http://{local_ip}:5000" target="_blank">http://{local_ip}:5000</a> or <a href="http://127.0.0.1:5000" target="_blank">http://127.0.0.1:5000</a></p>
            <p>Or view inline (may not work perfectly in all browsers):</p>
            <iframe src="http://127.0.0.1:5000" width="100%" height="800"></iframe>
        """))

        # Keep script alive (for non-Jupyter use)
        try:
            while True:
                time.sleep(1)
        except KeyboardInterrupt:
            logger.info("Shutting down Flask server...")
            flask_thread.join(timeout=5)
    except Exception as e:
        logger.error(f"Error starting Flask application: {e}")

2025-02-26 11:17:15,996 - INFO - Local IP detected: 192.168.244.41
2025-02-26 11:17:15,999 - ERROR - Error starting Flask application: name 'HTML' is not defined


 * Serving Flask app '__main__'
 * Debug mode: on


2025-02-26 11:17:16,214 - INFO - WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on all addresses (0.0.0.0)
 * Running on http://127.0.0.1:5000
 * Running on http://192.168.244.41:5000
2025-02-26 11:17:16,215 - INFO - Press CTRL+C to quit


In [5]:
from flask import Flask, render_template_string, request, jsonify
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.linear_model import LinearRegression
import threading
import time
import logging
from datetime import datetime
from IPython.display import display, HTML

# Configure logging
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Initialize Flask app
app = Flask(__name__)
app.secret_key = 'your_secure_secret_key_here'

# Global variables
trader = None
thread = None

# MLTrader class
class MLTrader:
    def __init__(self, symbol):
        self.symbol = symbol.upper()
        self.running = False
        self.trade_history = []
        self.inventory = []
        self.window_size = 10
        self.model = LinearRegression()
        self.data = self.load_data()
        self.last_trade_time = None

    def load_data(self):
        try:
            end_date = datetime.now().strftime('%Y-%m-%d')
            dataset = yf.download(self.symbol, start="2024-01-01", end=end_date, progress=False)
            if dataset.empty:
                logger.warning(f"No data available for {self.symbol}, using mock data")
                dates = pd.date_range('2025-02-10', '2025-02-24', freq='D')
                prices = [129.50, 130.00, 131.50, 132.00, 133.10, 134.00, 133.80, 132.90, 133.50, 132.00, 134.50, 134.43, 135.00, 134.20, 135.30]
                return pd.Series(prices, index=dates)
            return dataset['Close']
        except Exception as e:
            logger.error(f"Failed to load data for {self.symbol}: {e}")
            raise ValueError(f"Failed to load data for {self.symbol}: {str(e)}")

    def train(self):
        if len(self.data) < self.window_size + 1:
            raise ValueError(f"Data length ({len(self.data)}) is insufficient for window size {self.window_size}")
        X, y = [], []
        for i in range(len(self.data) - self.window_size):
            X.append(self.data.iloc[i:i + self.window_size].values)
            y.append(self.data.iloc[i + self.window_size])
        X = np.array(X).reshape(len(X), -1)
        y = np.array(y)
        self.model.fit(X, y)
        return f"Model R² Score: {self.model.score(X, y):.4f}"

    def predict(self, recent_data):
        if len(recent_data) < self.window_size:
            logger.warning(f"Insufficient data for prediction for {self.symbol}")
            return None
        return self.model.predict(np.array(recent_data).reshape(1, -1))[0]

    def get_realtime_price(self):
        try:
            latest_data = yf.download(self.symbol, period="1d", interval="1m", progress=False)["Close"]
            if not latest_data.empty:
                return latest_data.iloc[-1]
            raise ValueError(f"No price data available for {self.symbol}")
        except Exception as e:
            logger.error(f"Error fetching real-time price for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to fetch price for {self.symbol}: {str(e)}")

    def run(self):
        self.running = True
        try:
            self.data = self.load_data()
            self.train()
            recent_data = self.data.values[-self.window_size:]
            
            while self.running:
                try:
                    current_price = self.get_realtime_price()
                    if current_price is None:
                        logger.warning(f"No real-time price for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    predicted_price = self.predict(recent_data)
                    if predicted_price is None:
                        logger.warning(f"Prediction failed for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    if self.last_trade_time:
                        time_since_last_trade = (datetime.now() - self.last_trade_time).total_seconds()
                        if time_since_last_trade < 60:
                            time.sleep(60 - time_since_last_trade)

                    logger.debug(f"{self.symbol} - Current Price: ${current_price:.2f}, Predicted Price: ${predicted_price:.2f}")
                    
                    if predicted_price > current_price * 1.001 and not self.inventory:  # Buy if 0.1% above
                        self.inventory.append(current_price)
                        self.trade_history.append({
                            "time": datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
                            "action": f"BUY 10 shares of {self.symbol} at ${current_price:.2f}",
                            "price": current_price
                        })
                        self.last_trade_time = datetime.now()
                    elif predicted_price < current_price * 0.999 and self.inventory:  # Sell if 0.1% below
                        buy_price = self.inventory.pop(0)
                        profit = round(current_price - buy_price, 2)
                        self.trade_history.append({
                            "time": datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
                            "action": f"SELL 10 shares of {self.symbol} at ${current_price:.2f}",
                            "price": current_price
                        })
                        self.last_trade_time = datetime.now()

                    new_data = yf.download(self.symbol, start=datetime.now() - pd.Timedelta(days=1), end=datetime.now(), progress=False)["Close"]
                    if not new_data.empty:
                        self.data = pd.concat([self.data, new_data]).drop_duplicates()
                        recent_data = self.data.values[-self.window_size:]
                    time.sleep(60)  # Wait 60 seconds between checks
                except Exception as e:
                    logger.error(f"Error in trading loop for {self.symbol}: {str(e)}")
                    time.sleep(60)
                    continue
        except Exception as e:
            logger.error(f"Failed to start trading loop for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to start trading: {str(e)}")

    def stop(self):
        self.running = False
        logger.info(f"Stopped trading for {self.symbol}")

    def get_stats(self):
        latest_trade = self.trade_history[-1] if self.trade_history else None
        last_trade_time = (datetime.now() - self.last_trade_time).total_seconds() / 60 if self.last_trade_time else 0
        return {
            "latest_action": latest_trade["action"] if latest_trade else "None",
            "latest_price": f"${latest_trade['price']:.2f}" if latest_trade else "$0.00",
            "last_trade_time": f"{last_trade_time:.1f}" if last_trade_time > 0 else "0"
        }

# Flask routes
@app.route('/')
def home():
    return render_template_string(dashboard_html)

@app.route('/start_trading', methods=['POST'])
def start_trading():
    global trader, thread
    data = request.get_json()
    if not data:
        logger.error("No data provided in /start_trading request")
        return jsonify({'status': 'error', 'message': 'No data provided'}), 400

    stock_symbol = data.get('stock_symbol', '').strip()
    if not stock_symbol:
        logger.error("Stock symbol is required but not provided")
        return jsonify({'status': 'error', 'message': 'Stock symbol is required'}), 400

    if trader and trader.running:
        logger.warning(f"Bot already running for {trader.symbol}")
        return jsonify({'status': 'warning', 'message': f'Bot already running for {trader.symbol}'})

    try:
        trader = MLTrader(stock_symbol)
        logger.info(f"Starting bot for symbol: {stock_symbol}")
        thread = threading.Thread(target=trader.run, daemon=True)
        thread.start()
        return jsonify({'status': 'success', 'message': f'Trading started for {stock_symbol}'})
    except ValueError as e:
        logger.error(f"Error initializing trader for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 400
    except Exception as e:
        logger.error(f"Unexpected error starting trading for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 500

@app.route('/stop_trading', methods=['POST'])
def stop_trading():
    global trader, thread
    if trader and trader.running:
        trader.stop()
        if thread:
            thread.join(timeout=5)
        stats = trader.get_stats()
        trader = None
        thread = None
        logger.info("Bot stopped")
        return jsonify({'status': 'success', 'stats': stats})
    logger.warning("Bot not running")
    return jsonify({'status': 'warning', 'message': 'Bot is not running'})

@app.route('/status')
def status():
    if trader and trader.running:
        stats = trader.get_stats()
        return jsonify({'status': 'running', **stats})
    return jsonify({'status': 'stopped', 'latest_action': 'None', 'latest_price': '$0.00', 'last_trade_time': '0'})

# Dashboard HTML template as a string
dashboard_html = '''
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>ML Trading Bot Dashboard</title>
    <link href="https://cdn.jsdelivr.net/npm/tailwindcss@2.2.19/dist/tailwind.min.css" rel="stylesheet">
    <link href="https://fonts.googleapis.com/css2?family=Roboto:wght@400;700&display=swap" rel="stylesheet">
</head>
<body class="bg-black text-white">
    <div class="container mx-auto p-6">
        <h1 class="text-3xl font-bold mb-6 text-center">ML Trading Bot Dashboard</h1>
        <div class="controls bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <form id="tradingForm" method="POST" class="space-y-4">
                <div>
                    <label class="block text-sm font-medium mb-2">Stock Symbol</label>
                    <input type="text" name="stock_symbol" id="stock_symbol" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Stock Symbol (e.g., NVDA)" required pattern="[A-Z]{1,5}" title="Enter 1-5 uppercase letters (e.g., NVDA)">
                </div>
                <div class="flex space-x-4">
                    <button type="submit" name="action" value="start" class="w-full bg-green-600 hover:bg-green-700 text-white p-3 rounded font-bold transition-colors">Start Trading</button>
                    <button type="submit" name="action" value="stop" class="w-full bg-red-600 hover:bg-red-700 text-white p-3 rounded font-bold transition-colors">Stop Trading</button>
                </div>
            </form>
        </div>
        <div class="stats bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <h2 class="text-xl font-semibold mb-4">Latest Trade</h2>
            <p>Action: <span id="latest_action">None</span></p>
            <p>Price: <span id="latest_price">$0.00</span></p>
            <p>Last trade was <span id="last_trade_time">0</span> minutes ago</p>
        </div>
    </div>
    <script>
        async function updateStatus() {
            try {
                const response = await fetch('/status', { headers: { 'Accept': 'application/json' } });
                if (!response.ok) {
                    const text = await response.text();
                    throw new Error(`Server error: ${text || 'Failed to fetch status'}`);
                }
                const data = await response.json();
                document.getElementById('latest_action').textContent = data.latest_action;
                document.getElementById('latest_price').textContent = data.latest_price;
                document.getElementById('last_trade_time').textContent = data.last_trade_time;
            } catch (error) {
                console.error('Error updating status:', error);
                document.getElementById('latest_action').textContent = 'Error';
                document.getElementById('latest_price').textContent = '$0.00';
                document.getElementById('last_trade_time').textContent = '0';
                alert(`Status update failed: ${error.message}`);
            }
        }
        setInterval(updateStatus, 2000); // Update every 2 seconds
        updateStatus();

        document.getElementById('tradingForm').addEventListener('submit', async (e) => {
            e.preventDefault();
            const formData = new FormData(e.target);
            const stockSymbol = formData.get('stock_symbol')?.trim();
            const action = formData.get('action');
            if (!stockSymbol) {
                alert('Please enter a valid stock symbol (1-5 uppercase letters, e.g., NVDA)');
                return;
            }
            try {
                const response = await fetch(`/${action}_trading`, {
                    method: 'POST',
                    headers: { 'Content-Type': 'application/json', 'Accept': 'application/json' },
                    body: JSON.stringify({ stock_symbol: stockSymbol })
                });
                const data = await response.json();
                if (!response.ok) {
                    throw new Error(data.message || 'Server error');
                }
                alert(data.message);
                updateStatus(); // Refresh stats after action
            } catch (error) {
                console.error(`Error ${action} trading:`, error);
                alert(`Failed to ${action} trading: ${error.message}`);
            }
        });
    </script>
</body>
</html>
'''

# Function to run the Flask app in a separate thread
def run_flask():
    app.run(debug=True, use_reloader=False, host='0.0.0.0', port=5000)

# Start Flask in a separate thread
flask_thread = threading.Thread(target=run_flask, daemon=True)
flask_thread.start()

# Display the dashboard in an iframe
display(HTML(f"""
    <h2>ML Trading Bot Interface</h2>
    <p>Access the trading bot at <a href="http://127.0.0.1:5000" target="_blank">http://127.0.0.1:5000</a></p>
    <p>Or view inline (may not work perfectly in all browsers):</p>
    <iframe src="http://127.0.0.1:5000" width="100%" height="800"></iframe>
"""))

 * Serving Flask app '__main__'
 * Debug mode: on


2025-02-26 11:17:16,212 - INFO - WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on all addresses (0.0.0.0)
 * Running on http://127.0.0.1:5000
 * Running on http://192.168.244.41:5000
2025-02-26 11:17:16,214 - INFO - Press CTRL+C to quit


In [6]:
# Import necessary libraries
from IPython.display import HTML, display
import ipywidgets as widgets

# Define the HTML for the dashboard
dashboard_html = '''
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>Trading Bot Dashboard</title>
    <style>
        body {
            font-family: Arial, sans-serif;
            background-color: #0d1117;
            color: white;
            display: flex;
            justify-content: center;
            align-items: center;
            height: 100vh;
            margin: 0;
            flex-direction: column;
            transition: all 0.3s ease-in-out;
        }
        .container {
            width: 90%;
            max-width: 1200px;
            background: #161b22;
            padding: 20px;
            box-shadow: 0 0 15px rgba(255, 255, 255, 0.1);
            border-radius: 10px;
            text-align: center;
            transition: transform 0.3s ease-in-out;
        }
        .container:hover {
            transform: scale(1.02);
        }
        .grid {
            display: grid;
            grid-template-columns: repeat(3, 1fr);
            gap: 20px;
            margin-top: 20px;
        }
        .box {
            background: #21262d;
            color: #00ffcc;
            padding: 20px;
            border-radius: 10px;
            font-size: 1.5em;
            transition: transform 0.3s, background 0.3s;
        }
        .box:hover {
            transform: scale(1.05);
            background: #30363d;
        }
        input, button {
            padding: 10px;
            font-size: 1em;
            margin: 10px;
            border: none;
            border-radius: 5px;
        }
        button {
            background: #00ffcc;
            color: black;
            cursor: pointer;
            transition: background 0.3s;
        }
        button:hover {
            background: #00cca3;
        }
        canvas {
            margin-top: 20px;
            background: #21262d;
            border-radius: 10px;
        }
    </style>
</head>
<body>
    <div class="container">
        <h1>Trading Bot Dashboard</h1>
        <p>Enter your API keys and stock symbol below.</p>
        <input type="text" id="apiKey" placeholder="Alpaca API Key">
        <input type="text" id="apiSecret" placeholder="Alpaca Secret Key">
        <input type="text" id="stockSymbol" placeholder="Stock Symbol">
        <button onclick="startTrading()">Start Trading</button>
        <div class="grid">
            <div class="box" id="profit">Profit: $0</div>
            <div class="box" id="accuracy">Accuracy: 0%</div>
            <div class="box" id="trades">Live Trades: 0</div>
        </div>
        <canvas id="profitChart" width="400" height="200"></canvas>
    </div>

    <script src="https://cdn.jsdelivr.net/npm/chart.js"></script>
    <script>
        document.addEventListener("DOMContentLoaded", function() {
            updateChart();
        });

        function startTrading() {
            document.getElementById('profit').innerHTML = "Profit: $500";
            document.getElementById('accuracy').innerHTML = "Accuracy: 85%";
            document.getElementById('trades').innerHTML = "Live Trades: 15";
            updateChart();
        }

        function updateChart() {
            var ctx = document.getElementById('profitChart').getContext('2d');
            if (window.myChart) {
                window.myChart.destroy();
            }
            window.myChart = new Chart(ctx, {
                type: 'line',
                data: {
                    labels: ['Jan', 'Feb', 'Mar', 'Apr', 'May'],
                    datasets: [{
                        label: 'Profit ($)',
                        data: [100, 250, 400, 550, 700],
                        borderColor: '#00ffcc',
                        backgroundColor: 'rgba(0, 255, 204, 0.2)',
                        borderWidth: 2
                    }]
                },
                options: {
                    responsive: true,
                    scales: {
                        y: { beginAtZero: true }
                    }
                }
            });
        }
    </script>
</body>
</html>
'''

# Display the HTML dashboard in the notebook
display(HTML(dashboard_html))

In [7]:
from flask import Flask, render_template_string, request, jsonify
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.linear_model import LinearRegression
import threading
import time
import logging
from datetime import datetime
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import MarketOrderRequest
from alpaca.trading.enums import OrderSide, TimeInForce

# Configure logging
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Initialize Flask app
app = Flask(__name__)
app.secret_key = 'your_secure_secret_key_here'

# Global variables
trader = None
thread = None

# MLTrader class
class MLTrader:
    def __init__(self, symbol, api_key, secret_key):
        self.symbol = symbol.upper()
        self.api_key = api_key
        self.secret_key = secret_key
        self.running = False
        self.trade_history = []
        self.inventory = []
        self.window_size = 10
        self.model = LinearRegression()
        self.data = self.load_data()
        self.last_trade_time = None

        # Initialize TradingClient
        try:
            self.trading_client = TradingClient(self.api_key, self.secret_key, paper=True)
            logger.info(f"TradingClient initialized for {self.symbol}")
        except Exception as e:
            logger.error(f"Failed to initialize TradingClient: {str(e)}")
            raise ValueError(f"Failed to initialize TradingClient: {str(e)}")

    def load_data(self):
        try:
            end_date = datetime.now().strftime('%Y-%m-%d')
            dataset = yf.download(self.symbol, start="2024-01-01", end=end_date, progress=False)
            if dataset.empty:
                logger.warning(f"No data available for {self.symbol}, using mock data")
                dates = pd.date_range('2025-02-10', '2025-02-24', freq='D')
                prices = [129.50, 130.00, 131.50, 132.00, 133.10, 134.00, 133.80, 132.90, 133.50, 132.00, 134.50, 134.43, 135.00, 134.20, 135.30]
                return pd.Series(prices, index=dates)
            return dataset['Close']
        except Exception as e:
            logger.error(f"Failed to load data for {self.symbol}: {e}")
            raise ValueError(f"Failed to load data for {self.symbol}: {str(e)}")

    def train(self):
        if len(self.data) < self.window_size + 1:
            raise ValueError(f"Data length ({len(self.data)}) is insufficient for window size {self.window_size}")
        X, y = [], []
        for i in range(len(self.data) - self.window_size):
            X.append(self.data.iloc[i:i + self.window_size].values)
            y.append(self.data.iloc[i + self.window_size])
        X = np.array(X).reshape(len(X), -1)
        y = np.array(y)
        self.model.fit(X, y)
        logger.info(f"Model trained for {self.symbol}")
        return f"Model R² Score: {self.model.score(X, y):.4f}"

    def predict(self, recent_data):
        if len(recent_data) < self.window_size:
            logger.warning(f"Insufficient data for prediction for {self.symbol}")
            return None
        return self.model.predict(np.array(recent_data).reshape(1, -1))[0]

    def get_realtime_price(self):
        try:
            latest_data = yf.download(self.symbol, period="1d", interval="1m", progress=False)["Close"]
            if not latest_data.empty:
                return latest_data.iloc[-1]
            raise ValueError(f"No price data available for {self.symbol}")
        except Exception as e:
            logger.error(f"Error fetching real-time price for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to fetch price for {self.symbol}: {str(e)}")

    def place_order(self, qty, side):
        try:
            order_data = MarketOrderRequest(
                symbol=self.symbol,
                qty=qty,
                side=side,
                time_in_force=TimeInForce.DAY
            )
            order = self.trading_client.submit_order(order_data)
            logger.info(f"Order placed: {side} {qty} shares of {self.symbol}")
            return order
        except Exception as e:
            logger.error(f"Error placing {side} order for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to place order: {str(e)}")

    def run(self):
        self.running = True
        try:
            self.data = self.load_data()
            self.train()
            recent_data = self.data.values[-self.window_size:]
            
            while self.running:
                try:
                    current_price = self.get_realtime_price()
                    if current_price is None:
                        logger.warning(f"No real-time price for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    predicted_price = self.predict(recent_data)
                    if predicted_price is None:
                        logger.warning(f"Prediction failed for {self.symbol}, retrying in 60 seconds...")
                        time.sleep(60)
                        continue

                    if self.last_trade_time:
                        time_since_last_trade = (datetime.now() - self.last_trade_time).total_seconds()
                        if time_since_last_trade < 60:
                            time.sleep(60 - time_since_last_trade)

                    logger.debug(f"{self.symbol} - Current Price: ${current_price:.2f}, Predicted Price: ${predicted_price:.2f}")
                    
                    if predicted_price > current_price * 1.001 and not self.inventory:  # Buy if 0.1% above
                        self.place_order(10, OrderSide.BUY)
                        self.inventory.append(current_price)
                        self.trade_history.append({
                            "time": datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
                            "action": f"BUY 10 shares of {self.symbol} at ${current_price:.2f}",
                            "price": current_price
                        })
                        self.last_trade_time = datetime.now()
                    elif predicted_price < current_price * 0.999 and self.inventory:  # Sell if 0.1% below
                        self.place_order(10, OrderSide.SELL)
                        buy_price = self.inventory.pop(0)
                        profit = round(current_price - buy_price, 2)
                        self.trade_history.append({
                            "time": datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
                            "action": f"SELL 10 shares of {self.symbol} at ${current_price:.2f}",
                            "price": current_price
                        })
                        self.last_trade_time = datetime.now()

                    new_data = yf.download(self.symbol, start=datetime.now() - pd.Timedelta(days=1), end=datetime.now(), progress=False)["Close"]
                    if not new_data.empty:
                        self.data = pd.concat([self.data, new_data]).drop_duplicates()
                        recent_data = self.data.values[-self.window_size:]
                    time.sleep(60)  # Wait 60 seconds between checks
                except Exception as e:
                    logger.error(f"Error in trading loop for {self.symbol}: {str(e)}")
                    time.sleep(60)
                    continue
        except Exception as e:
            logger.error(f"Failed to start trading loop for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to start trading: {str(e)}")

    def stop(self):
        self.running = False
        logger.info(f"Stopped trading for {self.symbol}")

    def get_stats(self):
        latest_trade = self.trade_history[-1] if self.trade_history else None
        last_trade_time = (datetime.now() - self.last_trade_time).total_seconds() / 60 if self.last_trade_time else 0
        return {
            "latest_action": latest_trade["action"] if latest_trade else "None",
            "latest_price": f"${latest_trade['price']:.2f}" if latest_trade else "$0.00",
            "last_trade_time": f"{last_trade_time:.1f}" if last_trade_time > 0 else "0"
        }

# Flask routes
@app.route('/')
def home():
    return render_template_string(dashboard_html)

@app.route('/start_trading', methods=['POST'])
def start_trading():
    global trader, thread
    data = request.get_json()
    if not data:
        logger.error("No data provided in /start_trading request")
        return jsonify({'status': 'error', 'message': 'No data provided'}), 400

    stock_symbol = data.get('stock_symbol', '').strip()
    api_key = data.get('api_key', '').strip()
    secret_key = data.get('secret_key', '').strip()
    if not stock_symbol or not api_key or not secret_key:
        logger.error("Stock symbol, API key, and secret key are required")
        return jsonify({'status': 'error', 'message': 'Stock symbol, API key, and secret key are required'}), 400

    # Validate API keys by initializing the trading client
    try:
        test_client = TradingClient(api_key, secret_key, paper=True)
        account = test_client.get_account()
        logger.info(f"Connected to Alpaca account: {account.account_number}")
    except Exception as e:
        logger.error(f"Failed to initialize Alpaca client: {str(e)}")
        return jsonify({'status': 'error', 'message': 'Invalid API keys or Alpaca connection failed'}), 400

    if trader and trader.running:
        logger.warning(f"Bot already running for {trader.symbol}")
        return jsonify({'status': 'warning', 'message': f'Bot already running for {trader.symbol}'})

    try:
        trader = MLTrader(stock_symbol, api_key, secret_key)
        logger.info(f"Starting bot for symbol: {stock_symbol}")
        thread = threading.Thread(target=trader.run, daemon=True)
        thread.start()
        return jsonify({'status': 'success', 'message': f'Trading started for {stock_symbol}'})
    except ValueError as e:
        logger.error(f"Error initializing trader for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 400
    except Exception as e:
        logger.error(f"Unexpected error starting trading for {stock_symbol}: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 500

@app.route('/stop_trading', methods=['POST'])
def stop_trading():
    global trader, thread
    if trader and trader.running:
        trader.stop()
        if thread:
            thread.join(timeout=5)
        stats = trader.get_stats()
        trader = None
        thread = None
        logger.info("Bot stopped")
        return jsonify({'status': 'success', 'stats': stats})
    logger.warning("Bot not running")
    return jsonify({'status': 'warning', 'message': 'Bot is not running'})

@app.route('/status')
def status():
    if trader and trader.running:
        stats = trader.get_stats()
        return jsonify({'status': 'running', **stats})
    return jsonify({'status': 'stopped', 'latest_action': 'None', 'latest_price': '$0.00', 'last_trade_time': '0'})

# Dashboard HTML template as a string
dashboard_html = '''
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>ML Trading Bot Dashboard</title>
    <link href="https://cdn.jsdelivr.net/npm/tailwindcss@2.2.19/dist/tailwind.min.css" rel="stylesheet">
    <link href="https://fonts.googleapis.com/css2?family=Roboto:wght@400;700&display=swap" rel="stylesheet">
</head>
<body class="bg-black text-white">
    <div class="container mx-auto p-6">
        <h1 class="text-3xl font-bold mb-6 text-center">ML Trading Bot Dashboard</h1>
        <div class="controls bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <form id="tradingForm" method="POST" class="space-y-4">
                <div>
                    <label class="block text-sm font-medium mb-2">Stock Symbol</label>
                    <input type="text" name="stock_symbol" id="stock_symbol" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Stock Symbol (e.g., NVDA)" required pattern="[A-Z]{1,5}" title="Enter 1-5 uppercase letters (e.g., NVDA)">
                </div>
                <div>
                    <label class="block text-sm font-medium mb-2">API Key</label>
                    <input type="text" name="api_key" id="api_key" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter API Key" required>
                </div>
                <div>
                    <label class="block text-sm font-medium mb-2">Secret Key</label>
                    <input type="text" name="secret_key" id="secret_key" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Secret Key" required>
                </div>
                <div class="flex space-x-4">
                    <button type="submit" name="action" value="start" class="w-full bg-green-600 hover:bg-green-700 text-white p-3 rounded font-bold transition-colors">Start Trading</button>
                    <button type="submit" name="action" value="stop" class="w-full bg-red-600 hover:bg-red-700 text-white p-3 rounded font-bold transition-colors">Stop Trading</button>
                </div>
            </form>
        </div>
        <div class="stats bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <h2 class="text-xl font-semibold mb-4">Latest Trade</h2>
            <p>Action: <span id="latest_action">None</span></p>
            <p>Price: <span id="latest_price">$0.00</span></p>
            <p>Last trade was <span id="last_trade_time">0</span> minutes ago</p>
        </div>
    </div>
    <script>
        async function updateStatus() {
            try {
                const response = await fetch('/status', { headers: { 'Accept': 'application/json' } });
                if (!response.ok) {
                    const text = await response.text();
                    throw new Error(`Server error: ${text || 'Failed to fetch status'}`);
                }
                const data = await response.json();
                document.getElementById('latest_action').textContent = data.latest_action;
                document.getElementById('latest_price').textContent = data.latest_price;
                document.getElementById('last_trade_time').textContent = data.last_trade_time;
            } catch (error) {
                console.error('Error updating status:', error);
                document.getElementById('latest_action').textContent = 'Error';
                document.getElementById('latest_price').textContent = '$0.00';
                document.getElementById('last_trade_time').textContent = '0';
                alert(`Status update failed: ${error.message}`);
            }
        }
        setInterval(updateStatus, 2000); // Update every 2 seconds
        updateStatus();

        document.getElementById('tradingForm').addEventListener('submit', async (e) => {
            e.preventDefault();
            const formData = new FormData(e.target);
            const stockSymbol = formData.get('stock_symbol')?.trim();
            const apiKey = formData.get('api_key')?.trim();
            const secretKey = formData.get('secret_key')?.trim();
            const action = formData.get('action');
            if (!stockSymbol || !apiKey || !secretKey) {
                alert('Please enter a valid stock symbol, API key, and secret key');
                return;
            }
            try {
                const response = await fetch(`/${action}_trading`, {
                    method: 'POST',
                    headers: { 'Content-Type': 'application/json', 'Accept': 'application/json' },
                    body: JSON.stringify({ stock_symbol: stockSymbol, api_key: apiKey, secret_key: secretKey })
                });
                const data = await response.json();
                if (!response.ok) {
                    throw new Error(data.message || 'Server error');
                }
                alert(data.message);
                updateStatus(); // Refresh stats after action
            } catch (error) {
                console.error(`Error ${action} trading:`, error);
                alert(`Failed to ${action} trading: ${error.message}`);
            }
        });
    </script>
</body>
</html>
'''

# Run the Flask app
if __name__ == '__main__':
    app.run(debug=True, host='0.0.0.0', port=5000)

 * Serving Flask app '__main__'
 * Debug mode: on


2025-02-26 11:17:16,377 - INFO - WARNING: This is a development server. Do not use it in a production deployment. Use a production WSGI server instead.
 * Running on all addresses (0.0.0.0)
 * Running on http://127.0.0.1:5000
 * Running on http://192.168.244.41:5000
2025-02-26 11:17:16,378 - INFO - Press CTRL+C to quit
2025-02-26 11:17:16,393 - INFO -  * Restarting with watchdog (windowsapi)


SystemExit: 1

C:\Users\HP\AppData\Roaming\Python\Python312\site-packages\IPython\core\interactiveshell.py:3585: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [ ]:
from flask import Flask, render_template_string, request, jsonify
import os
import time
import numpy as np
import yfinance as yf
import pandas as pd
from sklearn.linear_model import LinearRegression
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import MarketOrderRequest
from alpaca.trading.enums import OrderSide, TimeInForce
import logging
import threading

# Configure logging
logging.basicConfig(filename='trading_bot.log', level=logging.INFO, format='%(asctime)s - %(message)s')
logger = logging.getLogger(__name__)

# Initialize Flask app
app = Flask(__name__)
app.secret_key = 'your_secure_secret_key_here'

# Global variables
trader = None
thread = None
trading_client = None

# Fetch API keys from environment variables
ALPACA_API_KEY = os.getenv("ALPACA_API_KEY")
ALPACA_SECRET_KEY = os.getenv("ALPACA_SECRET_KEY")
if ALPACA_API_KEY and ALPACA_SECRET_KEY:
    try:
        trading_client = TradingClient(ALPACA_API_KEY, ALPACA_SECRET_KEY, paper=True)
        logger.info("Alpaca Trading Client initialized successfully.")
    except Exception as e:
        logger.error(f"Failed to initialize Alpaca Trading Client: {str(e)}")
        trading_client = None
else:
    logger.warning("Alpaca API keys not found. Trading will be simulated.")

# Function to download stock data with retries
def dataset_loader(stock_name, max_retries=3):
    for attempt in range(1, max_retries + 1):
        try:
            dataset = yf.download(stock_name, start="2010-01-01", end="2025-01-01")
            if dataset.empty:
                raise ValueError(f"No data returned for {stock_name}")
            return dataset['Close']
        except Exception as e:
            logger.error(f"Failed to download {stock_name} data (attempt {attempt}/{max_retries}): {e}")
            time.sleep(2 ** attempt)  # Exponential backoff

    logger.warning(f"All retries failed. Falling back to mock data for {stock_name}.")
    return pd.Series(100 + np.cumsum(np.random.normal(0, 1, 100)))

# Place order function
def place_order(symbol, qty, side, limit_price):
    if trading_client:
        try:
            order_data = MarketOrderRequest(
                symbol=symbol,
                qty=qty,
                side=side,
                time_in_force=TimeInForce.DAY
            )
            order = trading_client.submit_order(order_data)
            logger.info(f"✅ REAL ORDER PLACED: {side} {qty} shares of {symbol} at ${round(limit_price, 2)}")
            return order
        except Exception as e:
            logger.error(f"❌ Error placing {side} order for {symbol}: {str(e)}")
            if hasattr(e, 'response') and hasattr(e.response, 'json'):
                logger.error(f"API Response: {e.response.json()}")
    else:
        logger.info(f"🔄 Simulated {side} order for {qty} shares of {symbol}.")

# Machine Learning Trader
class MLTrader:
    def __init__(self, symbol, window_size=10):
        self.symbol = symbol
        self.window_size = window_size
        self.model = LinearRegression()
        self.inventory = []
        self.running = False
        self.data = dataset_loader(symbol)
        self.train(self.data)

    def train(self, data):
        X, y = [], []
        for i in range(len(data) - self.window_size):
            X.append(data.iloc[i:i + self.window_size].values)
            y.append(data.iloc[i + self.window_size])
        X, y = np.array(X), np.array(y)
        if X.shape[0] > 0:
            self.model.fit(X, y)
        else:
            raise ValueError("Not enough data to train the model!")

    def predict(self, recent_data):
        return self.model.predict(np.array(recent_data).reshape(1, -1))[0]

    def run(self):
        self.running = True
        try:
            recent_data = self.data.values[-self.window_size:]
            while self.running:
                try:
                    current_price = self.data.iloc[-1]  # Use the latest price
                    predicted_price = self.predict(recent_data)

                    logger.debug(f"{self.symbol} - Current Price: ${current_price:.2f}, Predicted Price: ${predicted_price:.2f}")

                    # Buy Condition
                    if predicted_price > current_price * 1.001 and not self.inventory:
                        self.inventory.append(current_price)
                        logger.info(f"AI Trader bought: ${current_price:.2f}")
                        place_order(self.symbol, 10, OrderSide.BUY, current_price)

                    # Sell Condition
                    elif predicted_price < current_price * 0.999 and self.inventory:
                        buy_price = self.inventory.pop(0)
                        profit = round(current_price - buy_price, 2)
                        logger.info(f"AI Trader sold: ${current_price:.2f}, Profit: ${profit:.2f}")
                        place_order(self.symbol, 10, OrderSide.SELL, current_price)

                    # Update recent data
                    new_data = yf.download(self.symbol, period="1d", interval="1m", progress=False)["Close"]
                    if not new_data.empty:
                        self.data = pd.concat([self.data, new_data]).drop_duplicates()
                        recent_data = self.data.values[-self.window_size:]

                    time.sleep(60)  # Wait 60 seconds between checks
                except Exception as e:
                    logger.error(f"Error in trading loop for {self.symbol}: {str(e)}")
                    time.sleep(60)
                    continue
        except Exception as e:
            logger.error(f"Failed to start trading loop for {self.symbol}: {str(e)}")
            raise ValueError(f"Failed to start trading: {str(e)}")

    def stop(self):
        self.running = False
        logger.info("Trading bot stopped.")

# Flask routes
@app.route('/')
def home():
    return render_template_string(dashboard_html)

@app.route('/start_trading', methods=['POST'])
def start_trading():
    global trader, thread
    data = request.get_json()
    if not data:
        logger.error("No data provided in /start_trading request")
        return jsonify({'status': 'error', 'message': 'No data provided'}), 400

    stock_symbol = data.get('stock_symbol', '').strip()
    if not stock_symbol:
        logger.error("Stock symbol is required")
        return jsonify({'status': 'error', 'message': 'Stock symbol is required'}), 400

    if trader and trader.running:
        logger.warning(f"Bot already running for {trader.symbol}")
        return jsonify({'status': 'warning', 'message': f'Bot already running for {trader.symbol}'})

    try:
        trader = MLTrader(stock_symbol)
        logger.info(f"Starting bot for symbol: {stock_symbol}")
        thread = threading.Thread(target=trader.run, daemon=True)
        thread.start()
        return jsonify({'status': 'success', 'message': f'Trading started for {stock_symbol}'})
    except Exception as e:
        logger.error(f"Error starting trading bot: {str(e)}")
        return jsonify({'status': 'error', 'message': str(e)}), 500

@app.route('/stop_trading', methods=['POST'])
def stop_trading():
    global trader, thread
    if trader and trader.running:
        trader.stop()
        if thread:
            thread.join(timeout=5)
        trader = None
        thread = None
        logger.info("Bot stopped")
        return jsonify({'status': 'success', 'message': 'Trading stopped'})
    logger.warning("Bot is not running")
    return jsonify({'status': 'warning', 'message': 'Bot is not running'})

@app.route('/status')
def status():
    if trader and trader.running:
        return jsonify({'status': 'running', 'symbol': trader.symbol})
    return jsonify({'status': 'stopped'})

# Dashboard HTML template as a string
dashboard_html = '''
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>ML Trading Bot Dashboard</title>
    <link href="https://cdn.jsdelivr.net/npm/tailwindcss@2.2.19/dist/tailwind.min.css" rel="stylesheet">
    <link href="https://fonts.googleapis.com/css2?family=Roboto:wght@400;700&display=swap" rel="stylesheet">
</head>
<body class="bg-black text-white">
    <div class="container mx-auto p-6">
        <h1 class="text-3xl font-bold mb-6 text-center">ML Trading Bot Dashboard</h1>
        <div class="controls bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <form id="tradingForm" method="POST" class="space-y-4">
                <div>
                    <label class="block text-sm font-medium mb-2">Stock Symbol</label>
                    <input type="text" name="stock_symbol" id="stock_symbol" class="w-full p-3 bg-gray-800 rounded border-gray-700 text-white placeholder-gray-500" placeholder="Enter Stock Symbol (e.g., NVDA)" required pattern="[A-Z]{1,5}" title="Enter 1-5 uppercase letters (e.g., NVDA)">
                </div>
                <div class="flex space-x-4">
                    <button type="submit" name="action" value="start" class="w-full bg-green-600 hover:bg-green-700 text-white p-3 rounded font-bold transition-colors">Start Trading</button>
                    <button type="submit" name="action" value="stop" class="w-full bg-red-600 hover:bg-red-700 text-white p-3 rounded font-bold transition-colors">Stop Trading</button>
                </div>
            </form>
        </div>
        <div class="stats bg-gray-900 p-6 rounded-lg shadow-lg mb-6">
            <h2 class="text-xl font-semibold mb-4">Latest Trade</h2>
            <p>Status: <span id="status">Stopped</span></p>
            <p>Symbol: <span id="symbol">None</span></p>
        </div>
    </div>
    <script>
        async function updateStatus() {
            try {
                const response = await fetch('/status', { headers: { 'Accept': 'application/json' } });
                if (!response.ok) {
                    const text = await response.text();
                    throw new Error(`Server error: ${text || 'Failed to fetch status'}`);
                }
                const data = await response.json();
                document.getElementById('status').textContent = data.status;
                document.getElementById('symbol').textContent = data.symbol || 'None';
            } catch (error) {
                console.error('Error updating status:', error);
                document.getElementById('status').textContent = 'Error';
                document.getElementById('symbol').textContent = 'None';
                alert(`Status update failed: ${error.message}`);
            }
        }
        setInterval(updateStatus, 2000); // Update every 2 seconds
        updateStatus();

        document.getElementById('tradingForm').addEventListener('submit', async (e) => {
            e.preventDefault();
            const formData = new FormData(e.target);
            const stockSymbol = formData.get('stock_symbol')?.trim();
            const action = formData.get('action');
            if (!stockSymbol) {
                alert('Please enter a valid stock symbol (1-5 uppercase letters, e.g., NVDA)');
                return;
            }
            try {
                const response = await fetch(`/${action}_trading`, {
                    method: 'POST',
                    headers: { 'Content-Type': 'application/json', 'Accept': 'application/json' },
                    body: JSON.stringify({ stock_symbol: stockSymbol })
                });
                const data = await response.json();
                if (!response.ok) {
                    throw new Error(data.message || 'Server error');
                }
                alert(data.message);
                updateStatus(); // Refresh stats after action
            } catch (error) {
                console.error(`Error ${action} trading:`, error);
                alert(`Failed to ${action} trading: ${error.message}`);
            }
        });
    </script>
</body>
</html>
'''

# Run the Flask app
if __name__ == '__main__':
    app.run(debug=True, host='0.0.0.0', port=5000, use_reloader=False)

In [13]:
import os
import time
import numpy as np
import yfinance as yf
import pandas as pd
from sklearn.linear_model import LinearRegression
from alpaca.trading.client import TradingClient
from alpaca.trading.requests import LimitOrderRequest
from alpaca.trading.enums import OrderSide, TimeInForce
import logging
import threading
from IPython.display import display, clear_output, HTML

# Set up logging
logging.basicConfig(filename='trading_bot.log', level=logging.INFO, format='%(asctime)s - %(message)s')

# Global variables
trading_client = None
trader = None
data = None
stock_name = "NVDA"  # Default stock
window_size = 10
inventory = []
profit_loss = 0
running = False
trade_log = ["Trade Log:"]

# Fetch stock data
def dataset_loader(stock_name):
    try:
        dataset = yf.download(stock_name, start="2020-01-01", end=pd.Timestamp.today().strftime('%Y-%m-%d'))
        if dataset.empty:
            raise ValueError(f"No data returned for {stock_name}")
        return dataset['Close']
    except Exception as e:
        logging.error(f"Failed to download {stock_name}: {e}")
        return pd.Series(100 + np.cumsum(np.random.normal(0, 1, 100)))

# Place order
def place_order(symbol, qty, side, limit_price):
    global profit_loss
    if trading_client:
        try:
            order = LimitOrderRequest(
                symbol=symbol, qty=qty, side=side, time_in_force=TimeInForce.DAY, limit_price=round(limit_price, 2)
            )
            trading_client.submit_order(order)
            logging.info(f"REAL ORDER: {side} {qty} shares of {symbol} at ${limit_price}")
            update_log(f"{side} order placed for {symbol} at ${limit_price}")
        except Exception as e:
            logging.error(f"Error placing order: {e}")
    else:
        logging.info(f"Simulated {side} order for {qty} shares of {symbol}")
        update_log(f"Simulated {side} order for {symbol} at ${limit_price}")

# ML Trader class
class ML_Trader:
    def __init__(self, window_size=10):
        self.window_size = window_size
        self.model = LinearRegression()

    def train(self, data):
        X = [data.iloc[i:i + self.window_size].values for i in range(len(data) - self.window_size)]
        y = [data.iloc[i + self.window_size] for i in range(len(data) - self.window_size)]
        if X:
            self.model.fit(np.array(X), np.array(y))

    def predict(self, recent_data):
        return self.model.predict(np.array(recent_data).reshape(1, -1))[0]

# Update trade log
def update_log(message):
    trade_log.append(message)
    clear_output(wait=True)
    print(f"Profit & Loss: ${profit_loss:.2f}")
    print("\n".join(trade_log))

# Trading loop
def trading_loop():
    global profit_loss, inventory, data, trader, stock_name, running
    if trader is None or data is None or len(data) <= window_size:
        update_log("Error: Data or trader not initialized properly.")
        return
    while running:
        for t in range(window_size, len(data) - 1):
            if not running:
                break
            recent_data = data.iloc[t - window_size:t].values.flatten()
            predicted_price = trader.predict(recent_data).item()
            actual_price = round(data.iloc[t].item(), 2)

            time.sleep(5)  # Prevent wash trades

            if predicted_price > actual_price and not inventory:
                inventory.append(actual_price)
                place_order(stock_name, 10, OrderSide.BUY, actual_price)
                update_log(f"Bought {stock_name} at ${actual_price}")

            elif predicted_price < actual_price and inventory:
                time.sleep(10)  # Delay before selling
                buy_price = inventory.pop(0)
                profit = round(actual_price - buy_price, 2)
                profit_loss += profit * 10  # 10 shares
                place_order(stock_name, 10, OrderSide.SELL, actual_price)
                update_log(f"Sold {stock_name} at ${actual_price} (Profit: ${profit})")

# Manual input and control
def start_trading(api_key, secret_key, stock_symbol):
    global trading_client, stock_name, data, trader, running
    api_key = api_key.strip()
    secret_key = secret_key.strip()
    stock_name = stock_symbol.strip().upper()

    if not api_key or not secret_key or not stock_name:
        update_log("Error: All fields must be filled.")
        return

    try:
        trading_client = TradingClient(api_key, secret_key, paper=True)
        data = dataset_loader(stock_name)
        trader = ML_Trader(window_size)
        trader.train(data)
        running = True
        update_log(f"Started trading {stock_name}")
        threading.Thread(target=trading_loop, daemon=True).start()
    except Exception as e:
        update_log(f"Error starting trading: {str(e)}")
        running = False

def stop_trading():
    global running
    running = False
    update_log("Stopped trading")

# Initial prompt
print("Enter your trading details below:")
api_key = input("Alpaca API Key: ")
secret_key = input("Alpaca Secret Key: ")
stock_symbol = input("Stock Symbol (e.g., NVDA): ")

# Start trading with user input
start_trading(api_key, secret_key, stock_symbol)

# To stop, interrupt the kernel or manually call stop_trading() in another cell

Profit & Loss: $0.00
Trade Log:
Started trading AAPL


2025-02-26 11:22:38,892 - DEBUG - Starting new HTTPS connection (1): paper-api.alpaca.markets:443
2025-02-26 11:22:40,582 - DEBUG - https://paper-api.alpaca.markets:443 "POST /v2/orders HTTP/1.1" 200 858
2025-02-26 11:22:40,583 - INFO - REAL ORDER: OrderSide.BUY 10 shares of AAPL at $100.04


Profit & Loss: $0.00
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Profit & Loss: $0.00
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Bought AAPL at $100.04


2025-02-26 11:22:55,908 - DEBUG - https://paper-api.alpaca.markets:443 "POST /v2/orders HTTP/1.1" 403 293
2025-02-26 11:22:55,909 - ERROR - Error placing order: {"buy_limit_price":"100.04","code":40310000,"existing_order_id":"e3494efb-7c35-441b-b3bc-eab72a017107","message":"potential wash trade detected. use complex orders","reject_reason":"buy order exists, sell limit price should be greater than existing buy limit price","sell_limit_price":"99.42"}


Profit & Loss: $-6.20
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Bought AAPL at $100.04
Sold AAPL at $99.42 (Profit: $-0.62)


...

Profit & Loss: $-200.20
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Bought AAPL at $100.04
Sold AAPL at $99.42 (Profit: $-0.62)
OrderSide.BUY order placed for AAPL at $98.48
Bought AAPL at $98.48
Sold AAPL at $98.17 (Profit: $-0.31)
OrderSide.BUY order placed for AAPL at $97.97
Bought AAPL at $97.97
Sold AAPL at $95.16 (Profit: $-2.81)
OrderSide.BUY order placed for AAPL at $94.95
Bought AAPL at $94.95
Sold AAPL at $95.39 (Profit: $0.44)
OrderSide.BUY order placed for AAPL at $97.19
Bought AAPL at $97.19
Sold AAPL at $97.45 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $97.73
Bought AAPL at $97.73
Sold AAPL at $95.03 (Profit: $-2.7)
OrderSide.BUY order placed for AAPL at $95.02
Bought AAPL at $95.02
Sold AAPL at $95.72 (Profit: $0.7)
OrderSide.BUY order placed for AAPL at $94.13
Bought AAPL at $94.13
Sold AAPL at $94.39 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $94.58
Bought AAPL at $94.58
Sold AAPL at $92.72 (Profit: $-1.86)
Ord

2025-02-26 13:55:39,524 - DEBUG - https://paper-api.alpaca.markets:443 "POST /v2/orders HTTP/1.1" 200 857
2025-02-26 13:55:39,524 - INFO - REAL ORDER: OrderSide.BUY 10 shares of AAPL at $95.02


Profit & Loss: $-200.20
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Bought AAPL at $100.04
Sold AAPL at $99.42 (Profit: $-0.62)
OrderSide.BUY order placed for AAPL at $98.48
Bought AAPL at $98.48
Sold AAPL at $98.17 (Profit: $-0.31)
OrderSide.BUY order placed for AAPL at $97.97
Bought AAPL at $97.97
Sold AAPL at $95.16 (Profit: $-2.81)
OrderSide.BUY order placed for AAPL at $94.95
Bought AAPL at $94.95
Sold AAPL at $95.39 (Profit: $0.44)
OrderSide.BUY order placed for AAPL at $97.19
Bought AAPL at $97.19
Sold AAPL at $97.45 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $97.73
Bought AAPL at $97.73
Sold AAPL at $95.03 (Profit: $-2.7)
OrderSide.BUY order placed for AAPL at $95.02
Bought AAPL at $95.02
Sold AAPL at $95.72 (Profit: $0.7)
OrderSide.BUY order placed for AAPL at $94.13
Bought AAPL at $94.13
Sold AAPL at $94.39 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $94.58
Bought AAPL at $94.58
Sold AAPL at $92.72 (Profit: $-1.86)
Ord

2025-02-26 13:55:57,549 - DEBUG - https://paper-api.alpaca.markets:443 "POST /v2/orders HTTP/1.1" 403 292
2025-02-26 13:55:57,561 - ERROR - Error placing order: {"buy_limit_price":"97.97","code":40310000,"existing_order_id":"100cf51a-389e-49f0-9590-8e8315850da5","message":"potential wash trade detected. use complex orders","reject_reason":"buy order exists, sell limit price should be greater than existing buy limit price","sell_limit_price":"95.72"}


Profit & Loss: $-193.20
Trade Log:
Started trading AAPL
OrderSide.BUY order placed for AAPL at $100.04
Bought AAPL at $100.04
Sold AAPL at $99.42 (Profit: $-0.62)
OrderSide.BUY order placed for AAPL at $98.48
Bought AAPL at $98.48
Sold AAPL at $98.17 (Profit: $-0.31)
OrderSide.BUY order placed for AAPL at $97.97
Bought AAPL at $97.97
Sold AAPL at $95.16 (Profit: $-2.81)
OrderSide.BUY order placed for AAPL at $94.95
Bought AAPL at $94.95
Sold AAPL at $95.39 (Profit: $0.44)
OrderSide.BUY order placed for AAPL at $97.19
Bought AAPL at $97.19
Sold AAPL at $97.45 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $97.73
Bought AAPL at $97.73
Sold AAPL at $95.03 (Profit: $-2.7)
OrderSide.BUY order placed for AAPL at $95.02
Bought AAPL at $95.02
Sold AAPL at $95.72 (Profit: $0.7)
OrderSide.BUY order placed for AAPL at $94.13
Bought AAPL at $94.13
Sold AAPL at $94.39 (Profit: $0.26)
OrderSide.BUY order placed for AAPL at $94.58
Bought AAPL at $94.58
Sold AAPL at $92.72 (Profit: $-1.86)
Ord